# 各馬の戦績情報のスクレイピング

## スクレイピング対象の調査

In [1]:
import pandas as pd

import requests
from bs4 import BeautifulSoup
import time
from tqdm import tqdm # for prgress bar

In [2]:
race_id = '201901010101'
url = 'https://db.netkeiba.com/race/' + race_id
html = requests.get(url)
html.encoding = 'EUC-JP'
soup = BeautifulSoup(html.text, 'html.parser')

In [3]:
soup

<!DOCTYPE html PUBLIC "-//W3C//DTD XHTML 1.0 Transitional//EN" "http://www.w3.org/TR/xhtml1/DTD/xhtml1-transitional.dtd">

<html id="html" lang="ja" xml:lang="ja" xmlns="http://www.w3.org/1999/xhtml">
<head>
<title>2歳未勝利｜2019年7月27日 | 競馬データベース - netkeiba.com</title>
<meta content="IE=edge,chrome=1" http-equiv="X-UA-Compatible"/>
<meta content="ja" http-equiv="content-language">
<meta content="text/html; charset=utf-8" http-equiv="content-type"/>
<meta content="text/javascript" http-equiv="content-script-type"/>
<meta content="text/css" http-equiv="content-style-type"/>
<meta content="競馬データベースです。競走馬、騎手、レース、調教師、馬主。" name="description"/>
<meta content="競馬情報,競走馬,騎手,レース,調教師,検索,データベース,JRA,netkeiba.com" name="keywords"/>
<link href="https://cdn.netkeiba.com/img.db/common/css/reset.css?20160421" media="all" rel="stylesheet" type="text/css"/>
<link href="https://cdn.netkeiba.com/img.db/common/css/common.css?2020" media="all" rel="stylesheet" type="text/css"/>
<link href="https://cdn.netkeiba.com

In [4]:
import re

soup.find('table', attrs={'summary':'レース結果'}).find_all('a', attrs={'href': re.compile('^/horse')})

[<a href="/horse/2017105318/" id="umalink_201901010101" title="ゴルコンダ">ゴルコンダ</a>,
 <a href="/horse/2017104612/" id="umalink_201901010101" title="プントファイヤー">プントファイヤー</a>,
 <a href="/horse/2017103879/" id="umalink_201901010101" title="ラグリマスネグラス">ラグリマスネグラス</a>,
 <a href="/horse/2017106259/" id="umalink_201901010101" title="キタノコドウ">キタノコドウ</a>,
 <a href="/horse/2017104140/" id="umalink_201901010101" title="ネモフィラブルー">ネモフィラブルー</a>,
 <a href="/horse/2017101930/" id="umalink_201901010101" title="マイネルラクスマン">マイネルラクスマン</a>,
 <a href="/horse/2017100184/" id="umalink_201901010101" title="サンモンテベロ">サンモンテベロ</a>,
 <a href="/horse/2017102953/" id="umalink_201901010101" title="エスカレーション">エスカレーション</a>,
 <a href="/horse/2017102421/" id="umalink_201901010101" title="セイウンジュリア">セイウンジュリア</a>]

### 馬データとジョッキーデータのIDを収集する関数定義

In [5]:
def scrape_horse_and_jockey_data(race_id_list):
    
    race_results = {}
    
    for race_id in tqdm(race_id_list):
        try:
            url = 'https://db.netkeiba.com/race/' + race_id
            df = pd.read_html(url)[0]
            
            html = requests.get(url)
            html.encoding = 'EUC-JP'
            soup = BeautifulSoup(html.text, 'html.parser')
            
            horse_id_list = []
            jockey_id_list = []
    
            horse_list = soup.find('table', attrs={'summary':'レース結果'}).find_all('a', attrs={'href': re.compile('^/horse')})
            
            for a in horse_list:
                horse_id = re.findall(r'\d+', a['href'])
                horse_id_list.append(horse_id[0])
            
            jockey_list = soup.find('table', attrs={'summary':'レース結果'}).find_all('a', attrs={'href': re.compile('^/jockey')})
            
            for a in jockey_list:
                jockey_id = re.findall(r'\d+', a['href'])
                jockey_id_list.append(jockey_id[0])
                
            df['horse_id'] = horse_id_list
            df['jockey_id'] = jockey_id_list
            race_results[race_id] = df
            
            time.sleep(1)
                
        except IndexError:
            continue
        except Exception as e:
            print(e)
            break
        except:
                break
        
    return race_results

### 以前取得した結果からレースIDリストを作成し、スクレイピング開始

In [6]:
results  = pd.read_pickle('2019_result_raw.pickle')
race_id_list = results.index.unique()
race_id_list

Index(['201901010101', '201901010102', '201901010103', '201901010104',
       '201901010105', '201901010106', '201901010107', '201901010108',
       '201901010109', '201901010110',
       ...
       '201910021203', '201910021204', '201910021205', '201910021206',
       '201910021207', '201910021208', '201910021209', '201910021210',
       '201910021211', '201910021212'],
      dtype='object', length=3452)

In [7]:
horse_data = scrape_horse_and_jockey_data(race_id_list)

100%|█████████████████████████████████████| 3452/3452 [1:40:27<00:00,  1.75s/it]


In [18]:
#indexをrace_idにする
for key in horse_data:
    horse_data[key].index = [key] * len(horse_data[key])

#pd.DataFrame型にして一つのデータにまとめる
horse_data_df = pd.concat([horse_data[key] for key in horse_data])

In [19]:
horse_data_df

着順  枠番  馬番         馬名  性齢    斤量    騎手     タイム     着差     単勝  \
201901010101   1   1   1      ゴルコンダ  牡2  54.0  ルメール  1:48.3    NaN    1.4   
201901010101   2   3   3   プントファイヤー  牡2  54.0  岩田康誠  1:50.1      大    3.5   
201901010101   3   4   4  ラグリマスネグラス  牡2  51.0  団野大成  1:50.9      5   46.6   
201901010101   4   8   9     キタノコドウ  牡2  51.0  菅原明良  1:51.5  3.1/2   56.8   
201901010101   5   5   5   ネモフィラブルー  牡2  54.0  川島信二  1:51.7  1.1/2  140.3   
...           ..  ..  ..        ...  ..   ...   ...     ...    ...    ...   
201910021212  12   6  11   スリープレッピー  セ6  56.0  森裕太朗  2:45.7    1/2  120.3   
201910021212  13   1   1    バリオラージュ  牡5  54.0   斎藤新  2:46.0  1.3/4    7.5   
201910021212  14   2   3  サンライズアミーゴ  牡4  54.0  亀田温心  2:46.2      1   99.2   
201910021212  15   6  12        トロハ  牝3  52.0    武豊  2:46.2     クビ   17.5   
201910021212  16   2   4   ダイシンステルラ  牝4  55.0  川須栄彦  2:47.0      5  110.3   

                人気       馬体重       調教師    horse_id jockey_id  
201901010101   1.0  518(-16)  [東] 木村哲也  2017105318     05339  
201901010101   2.0   496(-8)  [東] 手塚貴久  2017104612     05203  
201901010101   6.0   546(+6)  [東] 藤沢和雄  2017103879     01180  
201901010101   7.0   458(-8)   [東] 高木登  2017106259     01179  
201901010101   9.0    436(0)  [西] 矢作芳人  2017104140     01062  
...            ...       ...       ...         ...       ...  
201910021212  15.0   458(+8)  [西] 藤沢則雄  2013104167     01165  
201910021212   4.0   460(+2)  [西] 角居勝彦  2014105643     01178  
201910021212  12.0  478(+14)  [西] 牧浦充徳  2015102081     01176  
201910021212   8.0   468(+2)  [西] 浜田多実  2016104221     00666  
201910021212  14.0   450(+8)  [西] 牧田和弥  2015100531     01128  

[47574 rows x 15 columns]

In [20]:
horse_data_df.to_pickle('2019_horse_id.pickle')

In [21]:
horse_id_list = horse_data_df['horse_id'].unique()

In [23]:
len(horse_id_list)

11557

In [30]:
url = 'https://db.netkeiba.com/horse/2017105318/'
pd.read_html(url)[3]

日付    開催 天気   R          レース名  映像  頭数  枠番  馬番  オッズ  ...   着差  \
0  2021/07/17  1福島5  晴   9  南相馬特別(1勝クラス) NaN  16   5  10  5.2  ...  0.9   
1  2020/12/26  5中山7  晴   9    立志賞(1勝クラス) NaN  18   6  12  3.5  ...  1.9   
2  2020/08/02  1札幌4  晴   7     3歳以上1勝クラス NaN   8   8   8  1.5  ...  0.2   
3  2019/08/31  2札幌5  曇  11     札幌2歳S(G3) NaN  12   7  10  1.8  ...  0.6   
4  2019/07/27  1札幌1  曇   1         2歳未勝利 NaN   9   1   1  1.4  ... -1.8   
5  2019/06/09  3東京4  曇   5          2歳新馬 NaN  11   4   4  4.8  ...  0.5   

   ﾀｲﾑ指数        通過        ペース    上り       馬体重 厩舎ｺﾒﾝﾄ  備考    勝ち馬(2着馬)     賞金  
0     **   3-3-3-2  34.9-35.9  36.5  532(-38)    NaN NaN   フィデリオグリーン    NaN  
1     **   1-1-1-1  37.5-36.8  38.7  570(+18)    NaN NaN     ルトロヴァイユ    NaN  
2     **   7-6-4-4  36.6-34.7  34.5  552(+28)    NaN NaN    シャムロックヒル  110.0  
3     **  10-7-7-2  36.0-37.3  37.3   524(+6)    NaN NaN     ブラックホール    NaN  
4     **   1-1-1-1  35.9-36.5  36.5  518(-16)    NaN NaN  (プントファイヤー)  500.0  
5     **     8-8-2  38.7-33.5  34.0    534(0)    NaN NaN        ワーケア  180.0  

[6 rows x 28 columns]

In [35]:
def scrape_horse_data(horse_id_list):
    
    horse_results = {}
    
    for horse_id in tqdm(horse_id_list):
        try:
            url = 'https://db.netkeiba.com/horse/' + horse_id
            df = pd.read_html(url)[3]
            if df.columns[0]=='受賞歴':
                df = pd.read_html(url)[4]
            
            horse_results[horse_id] = df
            
            time.sleep(1)
                
        except IndexError:
            continue
        except Exception as e:
            print(e)
            break
        except:
                break
        
    return horse_results

In [41]:
horse_results = scrape_horse_data(horse_id_list)

100%|███████████████████████████████████| 11557/11557 [4:48:16<00:00,  1.50s/it]


In [42]:
horse_results['2017105318']

日付    開催 天気   R          レース名  映像  頭数  枠番  馬番  オッズ  ...   着差  \
0  2021/07/17  1福島5  晴   9  南相馬特別(1勝クラス) NaN  16   5  10  5.2  ...  0.9   
1  2020/12/26  5中山7  晴   9    立志賞(1勝クラス) NaN  18   6  12  3.5  ...  1.9   
2  2020/08/02  1札幌4  晴   7     3歳以上1勝クラス NaN   8   8   8  1.5  ...  0.2   
3  2019/08/31  2札幌5  曇  11     札幌2歳S(G3) NaN  12   7  10  1.8  ...  0.6   
4  2019/07/27  1札幌1  曇   1         2歳未勝利 NaN   9   1   1  1.4  ... -1.8   
5  2019/06/09  3東京4  曇   5          2歳新馬 NaN  11   4   4  4.8  ...  0.5   

   ﾀｲﾑ指数        通過        ペース    上り       馬体重 厩舎ｺﾒﾝﾄ  備考    勝ち馬(2着馬)     賞金  
0     **   3-3-3-2  34.9-35.9  36.5  532(-38)    NaN NaN   フィデリオグリーン    NaN  
1     **   1-1-1-1  37.5-36.8  38.7  570(+18)    NaN NaN     ルトロヴァイユ    NaN  
2     **   7-6-4-4  36.6-34.7  34.5  552(+28)    NaN NaN    シャムロックヒル  110.0  
3     **  10-7-7-2  36.0-37.3  37.3   524(+6)    NaN NaN     ブラックホール    NaN  
4     **   1-1-1-1  35.9-36.5  36.5  518(-16)    NaN NaN  (プントファイヤー)  500.0  
5     **     8-8-2  38.7-33.5  34.0    534(0)    NaN NaN        ワーケア  180.0  

[6 rows x 28 columns]

In [50]:
horse_results

{'2017105318':                     日付    開催 天気   R          レース名  映像  頭数  枠番  馬番  オッズ  ...  \
 2017105318  2021/07/17  1福島5  晴   9  南相馬特別(1勝クラス) NaN  16   5  10  5.2  ...   
 2017105318  2020/12/26  5中山7  晴   9    立志賞(1勝クラス) NaN  18   6  12  3.5  ...   
 2017105318  2020/08/02  1札幌4  晴   7     3歳以上1勝クラス NaN   8   8   8  1.5  ...   
 2017105318  2019/08/31  2札幌5  曇  11     札幌2歳S(G3) NaN  12   7  10  1.8  ...   
 2017105318  2019/07/27  1札幌1  曇   1         2歳未勝利 NaN   9   1   1  1.4  ...   
 2017105318  2019/06/09  3東京4  曇   5          2歳新馬 NaN  11   4   4  4.8  ...   
 
              着差  ﾀｲﾑ指数        通過        ペース    上り       馬体重 厩舎ｺﾒﾝﾄ  備考  \
 2017105318  0.9     **   3-3-3-2  34.9-35.9  36.5  532(-38)    NaN NaN   
 2017105318  1.9     **   1-1-1-1  37.5-36.8  38.7  570(+18)    NaN NaN   
 2017105318  0.2     **   7-6-4-4  36.6-34.7  34.5  552(+28)    NaN NaN   
 2017105318  0.6     **  10-7-7-2  36.0-37.3  37.3   524(+6)    NaN NaN   
 2017105318 -1.8     **   1-1-1-1  35.9-36.5  36.

In [48]:
d = horse_results
for key in d: # key を取り出し
    d[key].index = [key] * len(d[key])
    
results = pd.concat([d[key] for key in d], sort = False)

# ファイルに保存
file_name = '2019_horse_raw.pickle'
results.to_pickle(file_name)

In [49]:
results

日付     開催  天気     R          レース名  映像    頭数   枠番    馬番  \
2017105318  2021/07/17   1福島5   晴   9.0  南相馬特別(1勝クラス) NaN  16.0  5.0  10.0   
2017105318  2020/12/26   5中山7   晴   9.0    立志賞(1勝クラス) NaN  18.0  6.0  12.0   
2017105318  2020/08/02   1札幌4   晴   7.0     3歳以上1勝クラス NaN   8.0  8.0   8.0   
2017105318  2019/08/31   2札幌5   曇  11.0     札幌2歳S(G3) NaN  12.0  7.0  10.0   
2017105318  2019/07/27   1札幌1   曇   1.0         2歳未勝利 NaN   9.0  1.0   1.0   
...                ...    ...  ..   ...           ...  ..   ...  ...   ...   
2017101106  2020/03/14   1阪神5   雨   2.0         3歳未勝利 NaN  13.0  6.0   9.0   
2017101106  2020/02/29   1中京1   曇   2.0         3歳未勝利 NaN  12.0  7.0  10.0   
2017101106  2020/02/09   2京都4   晴   2.0         3歳未勝利 NaN  15.0  2.0   3.0   
2017101106  2020/01/25   1京都8   曇   3.0         3歳未勝利 NaN  11.0  7.0   9.0   
2017101106  2019/09/01  2小倉12  小雨   5.0          2歳新馬 NaN  12.0  5.0   5.0   

              オッズ  ...  ﾀｲﾑ指数        通過        ペース    上り       馬体重 厩舎ｺﾒﾝﾄ  備考  \
2017105318    5.2  ...     **   3-3-3-2  34.9-35.9  36.5  532(-38)    NaN NaN   
2017105318    3.5  ...     **   1-1-1-1  37.5-36.8  38.7  570(+18)    NaN NaN   
2017105318    1.5  ...     **   7-6-4-4  36.6-34.7  34.5  552(+28)    NaN NaN   
2017105318    1.8  ...     **  10-7-7-2  36.0-37.3  37.3   524(+6)    NaN NaN   
2017105318    1.4  ...     **   1-1-1-1  35.9-36.5  36.5  518(-16)    NaN NaN   
...           ...  ...    ...       ...        ...   ...       ...    ...  ..   
2017101106  137.1  ...     **   5-5-6-7  38.3-37.1  38.2    460(0)    NaN NaN   
2017101106   45.4  ...     **  8-8-10-9  30.6-38.4  38.7   460(-2)    NaN NaN   
2017101106   40.9  ...     **   1-1-1-1  38.3-38.3  40.1    462(0)    NaN NaN   
2017101106   28.0  ...     **  10-9-9-7  36.9-37.8  38.3  462(+14)    NaN NaN   
2017101106  116.2  ...     **   4-6-7-5  37.7-36.9  38.1    448(0)    NaN NaN   

              勝ち馬(2着馬)     賞金  受賞歴  
2017105318   フィデリオグリーン    NaN  NaN  
2017105318     ルトロヴァイユ    NaN  NaN  
2017105318    シャムロックヒル  110.0  NaN  
2017105318     ブラックホール    NaN  NaN  
2017105318  (プントファイヤー)  500.0  NaN  
...                ...    ...  ...  
2017101106    サンライズプラウ    NaN  NaN  
2017101106   ワンダークンナパー    NaN  NaN  
2017101106    クールインパクト    NaN  NaN  
2017101106     フームスムート   51.0  NaN  
2017101106   ヴェルトライゼンデ    NaN  NaN  

[251661 rows x 29 columns]